In [1]:
#pip install numpy==1.9.3

In [26]:
import pandas as pd
import requests
import json 
import re
import os


In [27]:
def Find_url(string):
    regex = r"(?i)\b((?:https?://|www\d{0,3}[.]|[a-z0-9.\-]+[.][a-z]{2,4}/)(?:[^\s()<>]+|\(([^\s()<>]+|(\([^\s()<>]+\)))*\))+(?:\(([^\s()<>]+|(\([^\s()<>]+\)))*\)|[^\s`!()\[\]{};:'\".,<>?«»“”‘’]))"
    url = re.findall(regex,string)
    return [x[0] for x in url]

In [28]:
def open_url(zipcode):
    page = None
    main_path = '.\\'+"json_prob_files"
    try:
        url = "https://www.aponet.de/apotheke/apothekensuche?tx_aponetpharmacy_search%5Baction%5D=result&tx_aponetpharmacy_search%5Bcontroller%5D=Search&tx_aponetpharmacy_search%5Bsearch%5D%5Bplzort%5D="+zipcode+"&tx_aponetpharmacy_search%5Bsearch%5D%5Bstreet%5D=&tx_aponetpharmacy_search%5Bsearch%5D%5Bradius%5D=50&tx_aponetpharmacy_search%5Bsearch%5D%5Blat%5D=&tx_aponetpharmacy_search%5Bsearch%5D%5Blng%5D=&type=1981"
        page = requests.get(url)
        #print(page.text)
        data = json.loads(page.text)
        #print(data)
    except Exception as e:
        print(zipcode, "has a problem in json")
        s = page.text
        if os.path.isdir(main_path) == False:
            os.mkdir(main_path)
        #
        if s != None:
            wf = open("json_prob_files\\"+zipcode+".txt","w")
            wf.write(s)
        
        data = None
    return data


In [29]:
'''
if len(Find_url(data['features'][0]['properties']['popup'])) != 0:
    apo_url = Find_url(data['features'][0]['properties']['popup'])[0].split(';')[0][:-5]
else:
    apo_url = None
'''

"\nif len(Find_url(data['features'][0]['properties']['popup'])) != 0:\n    apo_url = Find_url(data['features'][0]['properties']['popup'])[0].split(';')[0][:-5]\nelse:\n    apo_url = None\n"

In [30]:
def extract_data(data):
    ls_dc = []
    #print(len(data['features']))
    for i in range(len(data['features'])):
        
        apothieka_name = data['features'][i]['properties']['name']
        apothieka_address = data['features'][i]['properties']['strasse']
        apothieka_plz = data['features'][i]['properties']['plz']
        apothieka_tel = data['features'][i]['properties']['telefon']
        apothieka_email = data['features'][i]['properties']['email']
    
        if len(Find_url(data['features'][i]['properties']['popup'])) != 0:
            apothieka_url = Find_url(data['features'][i]['properties']['popup'])[0].split(';')[0][:-5]
        else:
            apothieka_url = None
        
        ls_dc.append({'apothieka_name': apothieka_name,
                      'apothieka_address':apothieka_address,
                      'apothieka_plz': apothieka_plz,
                      'apothieka_tel': apothieka_tel,
                      'apothieka_email': apothieka_email,
                      'apothieka_url': apothieka_url,
                      })
  
    df = pd.DataFrame(ls_dc)
    return df


In [31]:
def main_process():
    combined_df = pd.DataFrame()
    old_df = pd.DataFrame()

    wf = open("notexist_zipcodes.txt","w")
    wfz = open("zipcodes.txt","w")
    txt = ""
    zip_txt = ''
    
    zipcodes_df = pd.read_excel("plz.xlsx", sheet_name='Tabelle1')
    
    for i in range(0,zipcodes_df.shape[0]):
        json_flag = False
        df = pd.DataFrame()
        data = open_url(str(zipcodes_df.loc[i].PLZ))
        zip_txt += str(zipcodes_df.loc[i].PLZ)
        
        if data != None:
            df = extract_data(data)
        elif data == None:
            json_flag = True
        
        if df.empty and json_flag == False:
            txt += str(zipcodes_df.loc[i].PLZ)+' zipcode not exist on the website \n'
        elif df.empty == False and json_flag == False:
            combined_df = old_df.append(df, ignore_index=True)
            combined_df.drop_duplicates(ignore_index=True, inplace= True)
            old_df = combined_df
            print(combined_df.info())

            
            
        
    wf.write(str (txt))
    wfz.write(str(zip_txt))
    wf.close()  
    wfz.close()
    
    return combined_df

In [32]:
'''
zipcodes_df = pd.read_excel("plz.xlsx", sheet_name='Tabelle1')
old_df = pd.DataFrame()
combined_df = pd.DataFrame()

for i in range(0,100):
    data = open_url(str(zipcodes_df.loc[i].PLZ))
    df = extract_data(data)
    combined_df = old_df.append(df, ignore_index=True)
    combined_df = combined_df.drop_duplicates(ignore_index=True)
    old_df = combined_df
    print(combined_df.info())
'''

'\nzipcodes_df = pd.read_excel("plz.xlsx", sheet_name=\'Tabelle1\')\nold_df = pd.DataFrame()\ncombined_df = pd.DataFrame()\n\nfor i in range(0,100):\n    data = open_url(str(zipcodes_df.loc[i].PLZ))\n    df = extract_data(data)\n    combined_df = old_df.append(df, ignore_index=True)\n    combined_df = combined_df.drop_duplicates(ignore_index=True)\n    old_df = combined_df\n    print(combined_df.info())\n'

In [33]:
df = main_process()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1027 entries, 0 to 1026
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1027 non-null   object
 1   apothieka_address  1027 non-null   object
 2   apothieka_plz      1027 non-null   object
 3   apothieka_tel      1027 non-null   object
 4   apothieka_email    1027 non-null   object
 5   apothieka_url      2 non-null      object
dtypes: object(6)
memory usage: 48.3+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1036 entries, 0 to 1035
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1036 non-null   object
 1   apothieka_address  1036 non-null   object
 2   apothieka_plz      1036 non-null   object
 3   apothieka_tel      1036 non-null   object
 4   apothieka_email    1036 non-null   object
 5   apothieka_url      2 non-null   

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1052 entries, 0 to 1051
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1052 non-null   object
 1   apothieka_address  1052 non-null   object
 2   apothieka_plz      1052 non-null   object
 3   apothieka_tel      1052 non-null   object
 4   apothieka_email    1052 non-null   object
 5   apothieka_url      2 non-null      object
dtypes: object(6)
memory usage: 49.4+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1052 entries, 0 to 1051
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1052 non-null   object
 1   apothieka_address  1052 non-null   object
 2   apothieka_plz      1052 non-null   object
 3   apothieka_tel      1052 non-null   object
 4   apothieka_email    1052 non-null   object
 5   apothieka_url      2 non-null   

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1056 entries, 0 to 1055
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1056 non-null   object
 1   apothieka_address  1056 non-null   object
 2   apothieka_plz      1056 non-null   object
 3   apothieka_tel      1056 non-null   object
 4   apothieka_email    1056 non-null   object
 5   apothieka_url      2 non-null      object
dtypes: object(6)
memory usage: 49.6+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1056 entries, 0 to 1055
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1056 non-null   object
 1   apothieka_address  1056 non-null   object
 2   apothieka_plz      1056 non-null   object
 3   apothieka_tel      1056 non-null   object
 4   apothieka_email    1056 non-null   object
 5   apothieka_url      2 non-null   

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1057 entries, 0 to 1056
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1057 non-null   object
 1   apothieka_address  1057 non-null   object
 2   apothieka_plz      1057 non-null   object
 3   apothieka_tel      1057 non-null   object
 4   apothieka_email    1057 non-null   object
 5   apothieka_url      2 non-null      object
dtypes: object(6)
memory usage: 49.7+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1057 entries, 0 to 1056
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1057 non-null   object
 1   apothieka_address  1057 non-null   object
 2   apothieka_plz      1057 non-null   object
 3   apothieka_tel      1057 non-null   object
 4   apothieka_email    1057 non-null   object
 5   apothieka_url      2 non-null   

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1057 entries, 0 to 1056
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1057 non-null   object
 1   apothieka_address  1057 non-null   object
 2   apothieka_plz      1057 non-null   object
 3   apothieka_tel      1057 non-null   object
 4   apothieka_email    1057 non-null   object
 5   apothieka_url      2 non-null      object
dtypes: object(6)
memory usage: 49.7+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1057 entries, 0 to 1056
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     1057 non-null   object
 1   apothieka_address  1057 non-null   object
 2   apothieka_plz      1057 non-null   object
 3   apothieka_tel      1057 non-null   object
 4   apothieka_email    1057 non-null   object
 5   apothieka_url      2 non-null   

...

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17699 entries, 0 to 17698
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17699 non-null  object
 1   apothieka_address  17699 non-null  object
 2   apothieka_plz      17699 non-null  object
 3   apothieka_tel      17699 non-null  object
 4   apothieka_email    17699 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 829.8+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17699 entries, 0 to 17698
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17699 non-null  object
 1   apothieka_address  17699 non-null  object
 2   apothieka_plz      17699 non-null  object
 3   apothieka_tel      17699 non-null  object
 4   apothieka_email    17699 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17729 entries, 0 to 17728
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17729 non-null  object
 1   apothieka_address  17729 non-null  object
 2   apothieka_plz      17729 non-null  object
 3   apothieka_tel      17729 non-null  object
 4   apothieka_email    17729 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 831.2+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17732 entries, 0 to 17731
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17732 non-null  object
 1   apothieka_address  17732 non-null  object
 2   apothieka_plz      17732 non-null  object
 3   apothieka_tel      17732 non-null  object
 4   apothieka_email    17732 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 835.6+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 835.6+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 835.6+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non

In [34]:
df.to_excel('apotheke.xlsx',  index=False)

In [35]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17823 entries, 0 to 17822
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17823 non-null  object
 1   apothieka_address  17823 non-null  object
 2   apothieka_plz      17823 non-null  object
 3   apothieka_tel      17823 non-null  object
 4   apothieka_email    17823 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 835.6+ KB


In [36]:
df.to_csv('apothieka.csv', index=False)

In [37]:
df.head()

apothieka_name   apothieka_address apothieka_plz  \
0                 Nordland Apotheke   Invalidenstr. 114         10115   
1                 Humboldt-Apotheke      Chausseestr. 7         10115   
2                Feuerland Apotheke   Chausseestraße 42         10115   
3  MediosApotheke Oranienburger Tor  Friedrichstr. 113a         10117   
4           Apotheke am Gartenplatz         Feldstr. 10         13355   

  apothieka_tel apothieka_email apothieka_url  
0       2823048                          None  
1       2828790                          None  
2      23458210                          None  
3       2833530                          None  
4       4639855                          None

In [38]:
file_name_ls = [ 15868, 15907,15910,15913,17033,17034,17036,17039,17087,17089,17091,17094,17098,17099,
17109,17111,17121,17126,17129,17139,17153,17154,17159,17166,17179,17217,17337,17349,17379,17389,17390,
17391,17392,17398,17406,17419,17429,17438,17440,17449,17454,17459,17489,17491,17493,17495,17498,
17506,17509,18334,18435,18437,18439,18461,18465,18507,18510,18513,18516,18519,18573,18574,18581,35579,35606,35614,
35619,35630,35638,35641,35647,35683,35684,35685,35686,35687,35688,35689,35708,35745,35753,35756,35759,35764,35767,35781,
35789,35792,35794,35796,35799,51545,51570,51597,51598,53179,53424,53426,53474,53489,53498,53545,53547,53557,53560,53562,53567,
53572,53577,53578,53579,53604,53619,53639,53773,53783,53809,55413,55422,55430,55432,56068,56070,56072,56073,56075,
56076,56077,56112,56130,56132,56133,56154,56170,56179,56182,56191,56203,56204,56206,56218,56220,56235,56237,56242,56244,56249,
56253,56254,56269,56271,56276,56281,56283,56290,56291,56294,56295,56299,56305,56307,56316,56317,56321,56322,56323,
56329,56330,56332,56333,56335,56337,56338,56340,56341,56346,56348,56349,56355,56357,56368,56370,56377,56379,56410,56412,56414,
56422,56424,56427,56428, 56457,56459,56462,56470,56472,56477,56479,56564,56566,56567,56575,56579,56581,56584,56587,56588,56589,56593,
56594,56598,56599,56626,56630,56637,56642,56645,56648,56651,56653,56656,56659,56727,56736,56743,56745,56751,56753,56754,56761,
56829,57072,57074,57080,57234,57258,57290,57299,57518,57520,57537,57539,57548,57555,57562,57567,57572,57577,57578,57580,57581,
57583,57584,57586,57587,57589,57610,57612,57614,57627,57629,57632,57635,57636,57638,57639,57641,57642,57644,57645,57647,57648,
61276,61279,65232,65307,65321,65326,65329,65388,65391,65510,65520,65527,65529,65549,65550,65551,65552,65553,65554,65555,65556,
65558,65582,65589,65594,65597,65599,65604,65606,65611,65614,65618,65620,65623,65624,65626,65627,65629]

In [42]:
def other_process():
    combined_df = pd.DataFrame()
    combined_df = df
    old_df = pd.DataFrame()
    old_df = df

    for f in file_name_ls:
        myfile=open("json_prob_files1\\"+str(f)+".txt","r")
        contents = myfile.read()         # read the entire file to string
        myfile.close()                   # close the file
        data = json.loads(contents)
        new_df = extract_data(data)
        combined_df = old_df.append(new_df, ignore_index=True)
        combined_df.drop_duplicates(ignore_index=True, inplace= True)
        old_df = combined_df
        print(combined_df.info())
    return combined_df        

In [43]:
new_df = other_process()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17826 entries, 0 to 17825
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17826 non-null  object
 1   apothieka_address  17826 non-null  object
 2   apothieka_plz      17826 non-null  object
 3   apothieka_tel      17826 non-null  object
 4   apothieka_email    17826 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 835.7+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17827 entries, 0 to 17826
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17827 non-null  object
 1   apothieka_address  17827 non-null  object
 2   apothieka_plz      17827 non-null  object
 3   apothieka_tel      17827 non-null  object
 4   apothieka_email    17827 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.0+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.0+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.0+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17833 entries, 0 to 17832
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17833 non-null  object
 1   apothieka_address  17833 non-null  object
 2   apothieka_plz      17833 non-null  object
 3   apothieka_tel      17833 non-null  object
 4   apothieka_email    17833 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

...

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non

In [44]:
new_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17835 entries, 0 to 17834
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   apothieka_name     17835 non-null  object
 1   apothieka_address  17835 non-null  object
 2   apothieka_plz      17835 non-null  object
 3   apothieka_tel      17835 non-null  object
 4   apothieka_email    17835 non-null  object
 5   apothieka_url      6360 non-null   object
dtypes: object(6)
memory usage: 836.1+ KB


In [45]:
new_df.to_excel('apotheke.xlsx',  index=False)

In [46]:
new_df.to_csv('apothieka.csv', index=False)